In [1]:
import pandas as pd
import numpy as np
import common

from pyecharts.charts import Grid, Kline, Line, Bar
from pyecharts import options as opts
from pyecharts.globals import ThemeType


In [2]:
label_period_candles = 24 * 15

In [3]:
df = common.read_kline_data('data/ETH_USDT_USDT-1h-futures.json')

In [4]:
df['target'] = df["close"].shift(-label_period_candles).rolling(label_period_candles).mean() / df["close"] - 1

In [5]:
df = df.iloc[-10000:]

In [6]:
data = []
for _, row in df.iterrows():
    data.append([
        row["open"], 
        row["close"], 
        row["low"], 
        row["high"], 
    ])

In [7]:
kline = (
    Kline(init_opts=opts.InitOpts(theme=ThemeType.CHALK))
    .add_xaxis(df["datetime"].tolist())
    .add_yaxis("K线图", data)
    .set_global_opts(
        xaxis_opts=opts.AxisOpts(is_scale=True),
        yaxis_opts=opts.AxisOpts(is_scale=True),
        title_opts=opts.TitleOpts(title="K线图"),

        datazoom_opts=[
            opts.DataZoomOpts(
                is_show=True,
                xaxis_index=[0, 1],
                type_="slider",
                pos_top="85%",
                range_start=98,
                range_end=100,
            ),
        ],
        # 十字线坐标
        tooltip_opts=opts.TooltipOpts(
            trigger="axis",
            axis_pointer_type="cross",
            # background_color="rgba(245, 245, 245, 0.8)",
            border_width=1,
            border_color="#ccc",
            textstyle_opts=opts.TextStyleOpts(color="#000"),
        ),
        # 上下十字线触发
        axispointer_opts=opts.AxisPointerOpts(
            is_show=True,
            link=[{"xAxisIndex": "all"}],
            label=opts.LabelOpts(background_color="#777"),
        ),      
    )
)

In [8]:
line = (
    Line()
    .add_xaxis(xaxis_data=df["datetime"].tolist())
    .add_yaxis(
        series_name="target",
        y_axis=df["target"].tolist(),
        xaxis_index=1,
        yaxis_index=1,
        label_opts=opts.LabelOpts(is_show=False),
    )
    .set_global_opts(
        xaxis_opts=opts.AxisOpts(
            type_="category",
            is_scale=True,
            grid_index=1,
            boundary_gap=False,
            axisline_opts=opts.AxisLineOpts(is_on_zero=False),
            axistick_opts=opts.AxisTickOpts(is_show=False),
            splitline_opts=opts.SplitLineOpts(is_show=False),
            axislabel_opts=opts.LabelOpts(is_show=False),
            split_number=20,
            min_="dataMin",
            max_="dataMax",
        ),
        yaxis_opts=opts.AxisOpts(
            grid_index=1,
            is_scale=True,
            split_number=2,
            # axislabel_opts=opts.LabelOpts(is_show=False),
            # axisline_opts=opts.AxisLineOpts(is_show=False),
            # axistick_opts=opts.AxisTickOpts(is_show=False),
            # splitline_opts=opts.SplitLineOpts(is_show=False),
        ),
        legend_opts=opts.LegendOpts(is_show=False),
    )
)

In [9]:
grid_chart = Grid()

In [10]:
grid_chart.add(
    kline,
    grid_opts=opts.GridOpts(pos_left="10%", pos_right="8%", height="50%"),
)

grid_chart.add(
    line,
    grid_opts=opts.GridOpts(
        pos_left="10%", pos_right="8%", pos_top="68%", height="16%"
    ),
)

In [11]:
grid_chart.render_notebook()

In [12]:
df["target"].std()

0.023595885594126564